In [23]:
# Import librairies

import pandas as pd

from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LinearRegression

import plotly.express as px
import plotly.graph_objects as go

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) # to avoid deprecation warnings

In [24]:
# URL of the CSV file of INSEE data
insee_url = 'https://medical-deserts-project.s3.eu-north-1.amazonaws.com/insee_clean.csv'

# Read the CSV file from the URL into a DataFrame
insee_df_original = pd.read_csv(insee_url, sep = ',', encoding='utf-8')

In [25]:
insee_df = insee_df_original.copy()

In [26]:
pd.set_option("display.max_columns", None)

In [27]:
# Remove useless columns
insee_df = insee_df.drop(["APL aux médecins généralistes de 65 ans et moins", "APL aux médecins généralistes de 62 ans et moins"], axis=1)

# APL column at the end of dataset
APL_column = insee_df.pop("APL aux médecins généralistes (sans borne d'âge)")
insee_df["APL aux médecins généralistes (sans borne d'âge)"] = APL_column

# Rename APL column
insee_df.rename(columns={"APL aux médecins généralistes (sans borne d'âge)": "APL"}, inplace=True)


In [28]:
print('Number of rows :', insee_df.shape[0])
print('Number of columns :', insee_df.shape[1])
print()

# Show first rows of the dataset
print('First rows of the dataset :')
display(insee_df.head())
print()

# Dataset statistics
print('Basics statistics :')
summary_stats_all = insee_df.describe(include='all')
display(summary_stats_all)
print()

# Missing values percentage
missing_percentages = (insee_df.isna().mean() * 100).round(2)
print('Percentage of missing values: ')
print(missing_percentages)

Number of rows : 38590
Number of columns : 88

First rows of the dataset :


Dynamique Entrepreneuriale  Dynamique Entrepreneuriale Service et Commerce  \
0                        57.0                                            23.0   
1                        45.0                                             4.0   
2                       634.0                                           828.0   
3                       113.0                                            62.0   
4                        42.0                                             1.0   

   Synergie Médicale COMMUNE           SEG Croissance POP  \
0                        114  en croissance démographique   
1                        143  en croissance démographique   
2                        366  en croissance démographique   
3                        132  en croissance démographique   
4                        121  en croissance démographique   

   Nb Omnipraticiens BV  Nb Infirmiers Libéraux BV  Nb dentistes Libéraux BV  \
0                     9                         14                         7   
1                    31                         36                        18   
2                    31                         36                        18   
3                    12                         12                         6   
4                    26                         21                        10   

   Nb pharmaciens Libéraux BV  Densité Médicale BV  \
0                           7             0.092860   
1                          18             0.099229   
2                          18             0.099229   
3                           6             1.000000   
4                          10             0.100905   

   Score équipement de santé BV  Indice Démographique  Nb Ménages  \
0                             4              44.19769         247   
1                             4              10.18071          67   
2                             4             696.92134        4640   
3                             1              85.77400         473   
4                             3               5.24276          41   

   Nb Résidences Principales  Nb propriétaire  Nb Logement  \
0                        248              196          289   
1                         67               61          142   
2                       4635             1968         5184   
3                        473              344          505   
4                         41               28           57   

   Nb Résidences Secondaires  Nb Log Vacants  \
0                         32               9   
1                         71               4   
2                        135             414   
3                         14              18   
4                         13               3   

   Nb Occupants Résidence Principale  Nb Entreprises Secteur Services  \
0                                728                              7.0   
1                                168                              4.0   
2                              11015                            342.0   
3                               1406                             22.0   
4                                 86                              1.0   

   Nb Entreprises Secteur Commerce  Nb Entreprises Secteur Construction  \
0                             11.0                                  2.0   
1                              0.0                                  1.0   
2                            301.0                                 58.0   
3                             26.0                                 17.0   
4                              0.0                                  0.0   

   Nb Entreprises Secteur Industrie  Nb Création Enteprises  \
0                               2.0                     4.0   
1                               0.0                     1.0   
2                             108.0                    83.0   
3                              10.0                     6.0   
4                               0.0                     0.0  


Basics statistics :


Dynamique Entrepreneuriale  \
count                 38590.000000   
unique                         NaN   
top                            NaN   
freq                           NaN   
mean                    122.059031   
std                     632.827660   
min                       1.000000   
25%                      20.000000   
50%                      33.000000   
75%                      75.000000   
max                   23794.000000   

        Dynamique Entrepreneuriale Service et Commerce  \
count                                     38590.000000   
unique                                             NaN   
top                                                NaN   
freq                                               NaN   
mean                                        131.970614   
std                                         948.912967   
min                                           0.000000   
25%                                           6.000000   
50%                                          13.000000   
75%                                          46.000000   
max                                       33506.000000   

        Synergie Médicale COMMUNE           SEG Croissance POP  \
count                38590.000000                        38590   
unique                        NaN                            2   
top                           NaN  en croissance démographique   
freq                          NaN                        38579   
mean                   107.723218                          NaN   
std                    230.556624                          NaN   
min                     13.000000                          NaN   
25%                     52.000000                          NaN   
50%                     72.000000                          NaN   
75%                    105.000000                          NaN   
max                   8419.000000                          NaN   

        Nb Omnipraticiens BV  Nb Infirmiers Libéraux BV  \
count           38590.000000               38590.000000   
unique                   NaN                        NaN   
top                      NaN                        NaN   
freq                     NaN                        NaN   
mean               16.670951                  16.542187   
std                12.968793                  14.425287   
min                 1.000000                   0.000000   
25%                 9.000000                   8.000000   
50%                12.000000                  12.000000   
75%                19.000000                  19.000000   
max                76.000000                 112.000000   

        Nb dentistes Libéraux BV  Nb pharmaciens Libéraux BV  \
count               38590.000000                38590.000000   
unique                       NaN                         NaN   
top                          NaN                         NaN   
freq                         NaN                         NaN   
mean                    8.038248                    8.038248   
std                     6.929272                    6.929272   
min                     0.000000                    0.000000   
25%                     4.000000                    4.000000   
50%                     6.000000                    6.000000   
75%                     9.000000                    9.000000   
max                    49.000000                   49.000000   

        Densité Médicale BV  Score équipement de santé BV  \
count          38590.000000                  38590.000000   
unique                  NaN                           NaN   
top                     NaN                           NaN   
freq                    NaN                           NaN   
mean               0.313389                      2.527961   
std                0.383459                      1.320803   
min                0.032518                      0.000000   
25%                0.083808                      1.000000   
50%                0.104593       


Percentage of missing values: 
Dynamique Entrepreneuriale                        0.0
Dynamique Entrepreneuriale Service et Commerce    0.0
Synergie Médicale COMMUNE                         0.0
SEG Croissance POP                                0.0
Nb Omnipraticiens BV                              0.0
                                                 ... 
Pop 15 ans ou plus Ouvriers en 2014 (compl)       0.0
Pop 15 ans ou plus Retraités  en 2014 (compl)     0.0
Pop 15 ans ou plus Autres en 2014 (compl)         0.0
taux chômage(15-64 ans)                           0.0
APL                                               0.0
Length: 88, dtype: float64


## Baseline model

In [29]:
# Separate target variable Y from features X
print("Separating labels from features...")
features_list = ["Pop 60-74 ans en 2014 (princ)"]
target_variable = "APL"

X = insee_df.loc[:,features_list]
Y = insee_df.loc[:,target_variable]

print("...Done.")
print()

print('Y : ')
print(Y.head())
print()
print('X :')
print(X.head())

Separating labels from features...
...Done.

Y : 
0    2.293
1    2.600
2    4.079
3    4.378
4    1.069
Name: APL, dtype: float64

X :
   Pop 60-74 ans en 2014 (princ)
0                          125.0
1                           33.0
2                         1853.0
3                          232.0
4                           27.0


In [30]:
#Train-test splitting

print("Dividing into train and test sets...")
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=0.2, random_state=42)
print("...Done.")
print()

Dividing into train and test sets...
...Done.



In [31]:
print("Preprocessing X_train...")
print(X_train.head())
print()
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
print("...Done!")
print(X_train[0:5,:]) # X_train is now a numpy array

print("Preprocessing X_test...")
print(X_test.head())
print()
X_test = scaler.transform(X_test) # don't fit again !
print("...Done!")
print(X_test[0:5,:]) # X_train is now a numpy array

Preprocessing X_train...
       Pop 60-74 ans en 2014 (princ)
19078                           78.0
7714                            74.0
3753                             8.0
10173                          111.0
26517                          316.0

...Done!
[[-0.18149761]
 [-0.18408344]
 [-0.22674955]
 [-0.16016456]
 [-0.02764103]]
Preprocessing X_test...
       Pop 60-74 ans en 2014 (princ)
32508                          488.0
6252                            42.0
29268                          284.0
217                             30.0
15576                          116.0

...Done!
[[ 0.08354944]
 [-0.20477004]
 [-0.04832763]
 [-0.21252751]
 [-0.15693227]]


In [32]:
# Train model
model = LinearRegression() # or LniearRegression pour regression lineaire par exemple
print("Training model...")
model.fit(X_train, Y_train)  # Training is always done on train set !!
print("...Done.")

Training model...
...Done.


In [33]:
# Print R^2 scores
print("R2 score on training set : ", model.score(X_train, Y_train))
print("R2 score on test set : ", model.score(X_test, Y_test))

R2 score on training set :  0.02391666410027038
R2 score on test set :  0.017773226632083805


In [34]:
# Predictions on training set
print("Predictions on training set...")
Y_train_pred = model.predict(X_train)
print("...Done.")
print(Y_train_pred)
print()

# Predictions on test set
print("Predictions on test set...")
Y_test_pred = model.predict(X_test)
print("...Done.")
print(Y_test_pred)
print()

Predictions on training set...
...Done.
[3.25538492 3.25487378 3.2464399  ... 3.37230917 3.7123479  3.26790796]

Predictions on test set...
...Done.
[3.30777721 3.25078463 3.28170885 ... 3.2537237  3.25014569 3.25167913]



In [35]:
# Visualize the model
# Visualize predictions on training Set
fig = px.scatter(x = X_train.flatten().tolist(), y = Y_train, title = "training set")
fig.add_trace(go.Scatter(x = X_train.flatten().tolist(), y = Y_train_pred, name = "linear regression"))
fig.show()

# Visualize predictions on test Set
fig = px.scatter(x = X_test.flatten().tolist(), y = Y_test, title = "test set")
fig.add_trace(go.Scatter(x = X_test.flatten().tolist(), y = Y_test_pred, name = "linear regression"))
fig.show()

## Multivariate model

In [36]:
# Separate target variable Y from features X
print("Separating labels from features...")
target_variable = "APL"

X = insee_df.drop(target_variable, axis = 1)
Y = insee_df.loc[:,target_variable]

print("...Done.")
print()

print('Y : ')
print(Y.head())
print()
print('X :')
X.head()

Separating labels from features...
...Done.

Y : 
0    2.293
1    2.600
2    4.079
3    4.378
4    1.069
Name: APL, dtype: float64

X :


Dynamique Entrepreneuriale  Dynamique Entrepreneuriale Service et Commerce  \
0                        57.0                                            23.0   
1                        45.0                                             4.0   
2                       634.0                                           828.0   
3                       113.0                                            62.0   
4                        42.0                                             1.0   

   Synergie Médicale COMMUNE           SEG Croissance POP  \
0                        114  en croissance démographique   
1                        143  en croissance démographique   
2                        366  en croissance démographique   
3                        132  en croissance démographique   
4                        121  en croissance démographique   

   Nb Omnipraticiens BV  Nb Infirmiers Libéraux BV  Nb dentistes Libéraux BV  \
0                     9                         14                         7   
1                    31                         36                        18   
2                    31                         36                        18   
3                    12                         12                         6   
4                    26                         21                        10   

   Nb pharmaciens Libéraux BV  Densité Médicale BV  \
0                           7             0.092860   
1                          18             0.099229   
2                          18             0.099229   
3                           6             1.000000   
4                          10             0.100905   

   Score équipement de santé BV  Indice Démographique  Nb Ménages  \
0                             4              44.19769         247   
1                             4              10.18071          67   
2                             4             696.92134        4640   
3                             1              85.77400         473   
4                             3               5.24276          41   

   Nb Résidences Principales  Nb propriétaire  Nb Logement  \
0                        248              196          289   
1                         67               61          142   
2                       4635             1968         5184   
3                        473              344          505   
4                         41               28           57   

   Nb Résidences Secondaires  Nb Log Vacants  \
0                         32               9   
1                         71               4   
2                        135             414   
3                         14              18   
4                         13               3   

   Nb Occupants Résidence Principale  Nb Entreprises Secteur Services  \
0                                728                              7.0   
1                                168                              4.0   
2                              11015                            342.0   
3                               1406                             22.0   
4                                 86                              1.0   

   Nb Entreprises Secteur Commerce  Nb Entreprises Secteur Construction  \
0                             11.0                                  2.0   
1                              0.0                                  1.0   
2                            301.0                                 58.0   
3                             26.0                                 17.0   
4                              0.0                                  0.0   

   Nb Entreprises Secteur Industrie  Nb Création Enteprises  \
0                               2.0                     4.0   
1                               0.0                     1.0   
2                             108.0                    83.0   
3                              10.0                     6.0   
4                               0.0                     0.0  

In [37]:
# Divide dataset Train set & Test set 
print("Dividing into train and test sets...")
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=0.2, random_state=42)
print("...Done.")
print()

Dividing into train and test sets...
...Done.



In [38]:
# Automatically detect names of numeric/categorical columns
numeric_features = []
categorical_features = []
for i, t in X.dtypes.items():
    if ('float' in str(t)) or ('int' in str(t)):
        numeric_features.append(i)
    else:
        categorical_features.append(i)
print('Found numeric features ', numeric_features)
print('Found categorical features ', categorical_features)

Found numeric features  ['Dynamique Entrepreneuriale', 'Dynamique Entrepreneuriale Service et Commerce', 'Synergie Médicale COMMUNE', 'Nb Omnipraticiens BV', 'Nb Infirmiers Libéraux BV', 'Nb dentistes Libéraux BV', 'Nb pharmaciens Libéraux BV', 'Densité Médicale BV', 'Score équipement de santé BV', 'Indice Démographique', 'Nb Ménages', 'Nb Résidences Principales', 'Nb propriétaire', 'Nb Logement', 'Nb Résidences Secondaires', 'Nb Log Vacants', 'Nb Occupants Résidence Principale', 'Nb Entreprises Secteur Services', 'Nb Entreprises Secteur Commerce', 'Nb Entreprises Secteur Construction', 'Nb Entreprises Secteur Industrie', 'Nb Création Enteprises', 'Nb Création Industrielles', 'Nb Création Construction', 'Nb Création Commerces', 'Nb Création Services', 'Moyenne Revenus Fiscaux Départementaux', 'Moyenne Revenus Fiscaux Régionaux', 'Dep Moyenne Salaires Horaires', 'Dep Moyenne Salaires Cadre Horaires', 'Dep Moyenne Salaires Prof Intermédiaire Horaires', 'Dep Moyenne Salaires Employé Horai

In [39]:
#Multiple Transformations preprocessing

# Create pipeline for numeric features
numeric_transformer = Pipeline(steps=[
    ('scaler', StandardScaler())
])

# Create pipeline for categorical features
categorical_transformer = Pipeline(
    steps=[
    ('encoder', OneHotEncoder(drop='first', handle_unknown='ignore')) # first column will be dropped to avoid creating correlations between features
    ])

# Use ColumnTransformer to make a preprocessor object that describes all the treatments to be done
preprocessor = ColumnTransformer(
    transformers=[
        ("num", numeric_transformer, numeric_features),
        ("cat", categorical_transformer, categorical_features),
    ]
)

In [40]:
# Preprocessings on train set
print("Performing preprocessings on train set...")
print(X_train.head())
X_train = preprocessor.fit_transform(X_train)
print('...Done.')
print(X_train[0:5,:])
print()

# Preprocessings on test set
print("Performing preprocessings on test set...")
print(X_test.head())
X_test = preprocessor.transform(X_test) # Don't fit again !!
print('...Done.')
print(X_test[0:5,:])
print()

Performing preprocessings on train set...
       Dynamique Entrepreneuriale  \
19078                        41.0   
7714                         40.0   
3753                         11.0   
10173                        63.0   
26517                        70.0   

       Dynamique Entrepreneuriale Service et Commerce  \
19078                                            16.0   
7714                                             14.0   
3753                                              1.0   
10173                                            10.0   
26517                                            55.0   

       Synergie Médicale COMMUNE           SEG Croissance POP  \
19078                         77  en croissance démographique   
7714                          46  en croissance démographique   
3753                          33  en croissance démographique   
10173                         97  en croissance démographique   
26517                         99  en croissance démographique   

 

In [41]:
# Train model
model = LinearRegression() # or LniearRegression pour regression lineaire par exemple
print("Training model...")
model.fit(X_train, Y_train)  # Training is always done on train set !!
print("...Done.")

Training model...
...Done.


In [42]:
# Print R^2 scores
print("R2 score on training set : ", model.score(X_train, Y_train))
print("R2 score on test set : ", model.score(X_test, Y_test))

R2 score on training set :  0.2409690103939559
R2 score on test set :  0.24180466141172086


In [43]:
# Predictions on training set
print("Predictions on training set...")
Y_train_pred = model.predict(X_train)
print("...Done.")
print(Y_train_pred)
print()

# Predictions on test set
print("Predictions on test set...")
Y_test_pred = model.predict(X_test)
print("...Done.")
print(Y_test_pred)
print()

Predictions on training set...
...Done.
[3.13455945 2.522033   2.32842792 ... 3.94241159 4.28724899 3.50833594]

Predictions on test set...
...Done.
[3.70642183 2.71470225 3.99322807 ... 3.52085077 2.73243294 3.17509212]



In [44]:
column_names = []
for name, pipeline, features_list in preprocessor.transformers_: # loop over pipelines
    if name == 'num': # if pipeline is for numeric variables
        features = features_list # just get the names of columns to which it has been applied
    else: # if pipeline is for categorical variables
        features = pipeline.named_steps['encoder'].get_feature_names_out() # get output columns names from OneHotEncoder
    column_names.extend(features) # concatenate features names
        
print("Names of columns corresponding to each coefficient: ", column_names)

# Create a pandas DataFrame
coefs = pd.DataFrame(index = column_names, data = model.coef_.transpose(), columns=["coefficients"])
coefs

# Compute abs() and sort values
feature_importance = abs(coefs).sort_values(by = 'coefficients')
feature_importance

# Plot coefficients
fig = px.bar(feature_importance, orientation = 'h')
fig.update_layout(showlegend = False, 
                  margin = {'l': 120} # to avoid cropping of column names
                 )

fig.update_layout(height=2400, width=1600)

fig.show()

Names of columns corresponding to each coefficient:  ['Dynamique Entrepreneuriale', 'Dynamique Entrepreneuriale Service et Commerce', 'Synergie Médicale COMMUNE', 'Nb Omnipraticiens BV', 'Nb Infirmiers Libéraux BV', 'Nb dentistes Libéraux BV', 'Nb pharmaciens Libéraux BV', 'Densité Médicale BV', 'Score équipement de santé BV', 'Indice Démographique', 'Nb Ménages', 'Nb Résidences Principales', 'Nb propriétaire', 'Nb Logement', 'Nb Résidences Secondaires', 'Nb Log Vacants', 'Nb Occupants Résidence Principale', 'Nb Entreprises Secteur Services', 'Nb Entreprises Secteur Commerce', 'Nb Entreprises Secteur Construction', 'Nb Entreprises Secteur Industrie', 'Nb Création Enteprises', 'Nb Création Industrielles', 'Nb Création Construction', 'Nb Création Commerces', 'Nb Création Services', 'Moyenne Revenus Fiscaux Départementaux', 'Moyenne Revenus Fiscaux Régionaux', 'Dep Moyenne Salaires Horaires', 'Dep Moyenne Salaires Cadre Horaires', 'Dep Moyenne Salaires Prof Intermédiaire Horaires', 'Dep M